In [56]:
import boto3
import logging
import os
import boto3.session
import random
import copy
import contextlib
import joblib
from tqdm import tqdm
from joblib import Parallel, delayed


In [57]:
s3 = boto3.resource('s3')

# Print out bucket names
bucket = s3.Bucket('buckfin')
obj = list(bucket.objects.filter(Prefix='t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/'))

In [58]:
setobjAWS = set([i.key.replace('t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/',"") for i in obj])
#print(setobjAWS)

In [59]:
setobjOS =set()
listobjOS = []

for path, currentDirectory, files in os.walk("/mnt/f/DataSet/DRDetectionKaggle/"):
    base = path.replace("/mnt/f/DataSet/DRDetectionKaggle/","")
    shortpath = list(map(lambda file: os.path.join(base,file), files))
    setobjOS = setobjOS.union(shortpath)
    listobjOS = listobjOS + list(shortpath)
#print(setobjOS)

In [60]:
print("Objet sur le disque", len(setobjOS))
print("Objet sur le disque liste", len(listobjOS))

###### Duplicate
seen = set()
dupes = []

for x in listobjOS:
    if x in seen:
        dupes.append(x)
    else:
        seen.add(x)
if dupes:
    print("Fichier doublon",dupes)
######
print("Objet sur le cloud",len(setobjAWS))
objtoupload = setobjOS.difference(setobjAWS)
print("Objet à upload",len(objtoupload))

Objet sur le disque 88704
Objet sur le disque liste 88704
Objet sur le cloud 24656
Objet à upload 64048


In [61]:
THREAD = 8
if len(objtoupload)<8:
    THREAD = len(objtoupload)
pool = copy.copy(objtoupload)
slen = int(len(objtoupload)/THREAD)
setthread = []
for i in range(THREAD):
    selectedset = set(random.sample(pool, slen))
    setthread.append(selectedset)
    pool -=  selectedset
taille = 0
for i in setthread:
    taille += len(i)
    print(len(i))
print(taille)

8006
8006
8006
8006
8006
8006
8006
8006
64048


In [62]:
def uploadset(objset):
    errorlist = []
    session = boto3.session.Session()
    s3 = session.resource('s3')
    bucket = s3.Bucket('buckfin')
    for shortname in objset:
        object_name = "t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/"+shortname
        file_name = "/mnt/f/DataSet/DRDetectionKaggle/"+shortname
        #print(file_name,object_name)
        try:
            response = bucket.upload_file(file_name, object_name)
        except ClientError as e:
            logging.error(e)
            errorlist.append((file_name,object_name,e))
            #print("ERROR",file_name,object)
    return errorlist

In [63]:
@contextlib.contextmanager
def tqdm_joblib(tqdm_object):
    """Context manager to patch joblib to report into tqdm progress bar given as argument"""
    class TqdmBatchCompletionCallback(joblib.parallel.BatchCompletionCallBack):
        def __call__(self, *args, **kwargs):
            tqdm_object.update(n=self.batch_size)
            return super().__call__(*args, **kwargs)

    old_batch_callback = joblib.parallel.BatchCompletionCallBack
    joblib.parallel.BatchCompletionCallBack = TqdmBatchCompletionCallback
    try:
        yield tqdm_object
    finally:
        joblib.parallel.BatchCompletionCallBack = old_batch_callback
        tqdm_object.close()

In [64]:
with tqdm_joblib(tqdm(desc="My calculation", total=THREAD)) as progress_bar:
    Parallel(n_jobs=THREAD)(delayed(uploadset)(i) for i in setthread)


/mnt/f/DataSet/DRDetectionKaggle/train/41804_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/41804_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/7608_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/7608_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/3249_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/3249_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/6571_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/6571_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/25777_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/25777_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/3484_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/3484_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/35203_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/35203_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/34083_right.jpeg t7fta73dp1/

My calculation:  12%|███████▋                                                     | 1/8 [5:59:20<41:55:20, 21560.14s/it]


/mnt/f/DataSet/DRDetectionKaggle/test/29532_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/29532_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/4255_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/4255_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/43365_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/43365_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/5515_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/5515_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/39911_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/39911_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/30107_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/30107_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/40541_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/40541_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/41537_left.jpeg t7fta73

My calculation:  25%|███████████████▌                                              | 2/8 [5:59:42<14:49:04, 8890.71s/it]

 t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/27140_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/34913_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/34913_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/32181_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/32181_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/23131_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/23131_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/25824_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/25824_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/42530_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/42530_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/9059_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/9059_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/38359_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k

...

My calculation:  62%|███████████████████████████████████████▍                       | 5/8 [6:01:25<1:35:10, 1903.44s/it]

 t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/39685_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/25270_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/25270_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/22938_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/22938_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/21889_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/21889_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/24283_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/24283_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/33139_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/33139_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/32001_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/train/32001_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/43391_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/tr

My calculation:  75%|████████████████████████████████████████████████▊                | 6/8 [6:02:28<42:35, 1277.81s/it]


/mnt/f/DataSet/DRDetectionKaggle/test/21157_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/21157_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/24005_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/24005_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/22435_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/22435_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/27044_left.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/27044_left.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/26386_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/26386_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/35520_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/35520_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/test/53_right.jpeg t7fta73dp1/datasets/dsscf9n1b9ryofk/versions/x99k71e/data/test/53_right.jpeg
/mnt/f/DataSet/DRDetectionKaggle/train/38833_left.jpeg t7fta73dp1/

My calculation: 100%|█████████████████████████████████████████████████████████████████| 8/8 [6:02:54<00:00, 2721.76s/it]
